<a href="https://colab.research.google.com/github/fdonadio1979/account_check/blob/master/Cintelink_db.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
%%shell
cat /proc/cpuinfo |& head -10

processor	: 0
vendor_id	: GenuineIntel
cpu family	: 6
model		: 63
model name	: Intel(R) Xeon(R) CPU @ 2.30GHz
stepping	: 0
microcode	: 0x1
cpu MHz		: 2299.998
cache size	: 46080 KB
physical id	: 0


In [ ]:
!pip install sshtunnel
!pip install pymysql
!pip install plotly_express

     |████████████████████████████████| 215kB 7.4MB/s 
     |████████████████████████████████| 3.2MB 9.7MB/s 
     |████████████████████████████████| 71kB 5.9MB/s 
     |████████████████████████████████| 962kB 39.6MB/s 
     |████████████████████████████████| 51kB 2.6MB/s 


In [ ]:
REMOTE_IP = '142.93.78.3' # 'boson.cintelink.com.ar'
#REMOTE_IP = '35.174.147.169' #nucleon

REMOTE_PORT = 22
LOCAL_IP = '127.0.0.1'
LOCAL_PORT = 3306

USER = 'fdonadio'

from getpass import getpass
PASS = getpass('Enter the PASS value: ')

In [12]:
from sshtunnel import SSHTunnelForwarder

server = SSHTunnelForwarder(
    (REMOTE_IP, REMOTE_PORT),
    ssh_username=USER,
    ssh_password=PASS,
    remote_bind_address=(LOCAL_IP, LOCAL_PORT)
)

server.start()
server_port = server.local_bind_port

In [5]:
DB_USER = 'cintelink'
DB_NAME = 'cintelink_dev' #boson
#DB_NAME = 'cintelink_db' #nucleon
DB_HOST = '127.0.0.1'
from getpass import getpass
DB_PASS = getpass('Enter the secret value: ')


Enter the secret value: ··········


In [6]:
import pandas as pd
import pymysql
connection = pymysql.connect(
    host = DB_HOST,
    user = DB_USER,
    password = DB_PASS,
    database = DB_NAME,
    port = server.local_bind_port
)

sql = "SELECT   `descripcion` , `id_equipo`, `online` , `current_firmware` , `ultima_sincronizacion` , `geo_latitude` , `geo_longitude` FROM `fs_equipo` WHERE `baja` =0"
fs_equipo = pd.read_sql(sql, con = connection)
sql = "SELECT `tanque` , `tanque_status_power` , `tanque_rssi_sonda` , `tanque_status_offline` , `tanque_ultima_actualizacion` , `id_tanque` , `cantidad` FROM `fs_tanques` WHERE `id_equipo` = 800 AND `baja` =0"
fs_tanques = pd.read_sql(sql, con = connection)
sql = "SELECT `id_equipo`,`fecha`,`hora`,`volumen`,`temperatura`,`codigo`,`vbat1`,`vbat2`,`fuel_level_dmm`,`producto`,`tank_site_id` FROM sis_historial_2021_4 WHERE `id_equipo` =800 AND `fecha` BETWEEN '2021-04-01' AND '2021-04-20'"
sis_historial_2021_4 = pd.read_sql(sql, con = connection)
sql = "SELECT * FROM `fs_sensores_sonda` WHERE `id_equipo` =800"
fs_sensores_sonda = pd.read_sql(sql, con = connection)




In [42]:
import pandas as pd
import pymysql
connection = pymysql.connect(
    host = DB_HOST,
    user = DB_USER,
    password = DB_PASS,
    database = DB_NAME,
    port = server.local_bind_port
)

site = "800";

year = "2020";
index = "1"  
sql = 'SELECT `id_equipo`,`fecha`,`hora`,`volumen`,`temperatura`,`codigo`,`vbat1`,`vbat2`,`fuel_level_dmm`,`producto`,`tank_site_id` FROM sis_historial_' + year +'_' + index +' WHERE `id_equipo` IN (' + site + ')'
#print (sql)
sis_historial_acc = pd.read_sql(sql, con = connection)
for i in range(11):
  index = str(i+2)
  sql = 'SELECT `id_equipo`,`fecha`,`hora`,`volumen`,`temperatura`,`codigo`,`vbat1`,`vbat2`,`fuel_level_dmm`,`producto`,`tank_site_id` FROM sis_historial_' + year +'_' + index +' WHERE `id_equipo` IN (' + site + ')'
 # print (sql)
  sis_historial = pd.read_sql(sql, con = connection)
  sis_historial_acc = [sis_historial_acc,sis_historial]
  sis_historial_acc = pd.concat(sis_historial_acc)

year = "2021";
for i in range(pd.to_datetime('now').month):
  index = str(i+1)
  sql = 'SELECT `id_equipo`,`fecha`,`hora`,`volumen`,`temperatura`,`codigo`,`vbat1`,`vbat2`,`fuel_level_dmm`,`producto`,`tank_site_id` FROM sis_historial_' + year +'_' + index +' WHERE `id_equipo` IN (' + site + ')'
#  print (sql)
  sis_historial = pd.read_sql(sql, con = connection)
  sis_historial_acc = [sis_historial_acc,sis_historial]
  sis_historial_acc = pd.concat(sis_historial_acc)
#  df=[sis_historial[['timestamp','fuel_level_dmm','tank_site_id']],df]
#  df=pd.concat(df)
sis_historial_acc[sis_historial_acc.filter(regex='volumen|temperatura|vbat1|vbat2|fuel_level_dmm|producto').columns]=sis_historial_acc[sis_historial_2021_4.filter(regex='volumen|temperatura|vbat1|vbat2|fuel_level_dmm|producto').columns].apply(pd.to_numeric, errors='coerce', axis=1)
sis_historial_acc['timestamp'] = pd.to_datetime(sis_historial_acc['fecha'])+sis_historial_acc['hora']
#df.info()

In [43]:
import pandas as pd 
import plotly.graph_objects as go 
import plotly_express as px
from plotly.subplots import make_subplots

df=sis_historial_acc[['timestamp','fuel_level_dmm','vbat2','tank_site_id']]

df = df.groupby(['tank_site_id', pd.Grouper(key='timestamp', freq='s')]).agg({'fuel_level_dmm':'sum', 'vbat2':'sum'}).reset_index()
df

tank_site_id           timestamp  fuel_level_dmm  vbat2
0                01 2021-02-01 00:00:40         10372.0  305.0
1                01 2021-02-01 00:01:39         10372.0  306.0
2                01 2021-02-01 00:02:38         10372.0  306.0
3                01 2021-02-01 00:03:37         10372.0  306.0
4                01 2021-02-01 00:05:34         10372.0  306.0
...             ...                 ...             ...    ...
560955           06 2021-04-07 12:56:07         11439.0  303.0
560956           06 2021-04-07 12:57:06         11438.0  303.0
560957           06 2021-04-07 12:58:05         11438.0  304.0
560958           06 2021-04-07 12:59:04         11438.0  303.0
560959           06 2021-04-07 13:00:03         11438.0  303.0

[560960 rows x 4 columns]

In [44]:
for i in range(9):
  index = str(i+1)
  df['tank_site_id'] = df['tank_site_id'].replace([index], '0'+index)

df.sort_values(by=['tank_site_id', 'timestamp'], axis = 0, ascending = True,
                 inplace = True, na_position ='last')

In [45]:
# create a blank canvas

#https://stackoverflow.com/questions/62428052/any-way-to-input-dynamic-amount-of-secondary-ytrue-in-the-specs-of-make-sub

fig = go.Figure()


#fig = make_subplots(rows=len(df.tank_site_id.unique()), cols=1,shared_xaxes=True,specs="secondary_y": True)
fig = make_subplots(
    rows=len(df.tank_site_id.unique()),
    cols=1,
    shared_xaxes=True ,
    shared_yaxes=True,
    specs = list([[{ 'secondary_y':True }]]*len(df.tank_site_id.unique())))  





for i, tank in enumerate(df.tank_site_id.unique()):
  fig.add_trace(
          go.Scatter(
                x=df[df['tank_site_id']==tank]['timestamp']
              , y=df[df['tank_site_id']==tank]['fuel_level_dmm']
              , mode='markers'
              , name='Tank '+tank+': fuel_level_dmm'
              , marker_size=2
          )
          , row=i+1
          , col=1
          , secondary_y=False
          )
  fig.add_trace(
          go.Scatter(
                x=df[df['tank_site_id']==tank]['timestamp']
              , y=df[df['tank_site_id']==tank]['vbat2']
              , mode='markers'
              , name='Tank '+tank+': vbat2'
              , marker_size=2
          )
          , row=i+1
          , col=1
          , secondary_y=True
          )
#https://plotly.com/python/reference/layout/#layout-autosize
fig.update_layout(
    height=800,
    font_family='Times New Roman',
    font_size=11
)

fig.update_xaxes(
    nticks=30

)

fig.update_yaxes(
    nticks=5,

)


fig.show()

In [46]:
fig = go.Figure()


#fig = make_subplots(rows=len(df.tank_site_id.unique()), cols=1,shared_xaxes=True,specs="secondary_y": True)
fig = make_subplots(
    rows=1,
    cols=1,
    shared_xaxes=True ,
    specs = [[{ 'secondary_y':True }]]
)

tank = '01'


fig.add_trace(
        go.Scatter(
#        go.bar(
              x=df[df['tank_site_id']==tank]['timestamp']
            , y=df[df['tank_site_id']==tank]['fuel_level_dmm']
            , mode='markers'
            , name='Tank '+tank+': fuel_level_dmm'
            , marker_size=2
        )
        , row=1
        , col=1
        , secondary_y=False
        )
fig.add_trace(
        go.Scatter(
              x=df[df['tank_site_id']==tank]['timestamp']
            , y=df[df['tank_site_id']==tank]['vbat2']
            , mode='markers'
            , name='Tank '+tank+': vbat2'
            , marker_size=2
        )
        , row=1
        , col=1
        , secondary_y=True
        )

fig.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1d", step="day", stepmode="backward"),
            dict(count=7, label="1w", step="day", stepmode="backward"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    )
)

fig.show()